### Requirements

In [1]:
!pip install POT
!pip install opencv-python
!pip install gudhi
!pip install scipy
!pip install GPyOpt

   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 835.4/835.4 kB 21.2 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 3.3/3.3 MB 23.5 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 56.8/56.8 kB 3.5 MB/s eta 0:00:00
  Preparing metadata (setup.py) ... done
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 60.4/60.4 kB 3.9 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 3.6/3.6 MB 47.8 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 38.4/38.4 MB 11.9 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 103.2/103.2 kB 6.4 MB/s eta 0:00:00
  Created wheel for GPyOpt: filename=GPyOpt-1.2.6-py3-none-any.whl size=83602 sha256=f86abbb366e31cba88ac4d22c2c0dfcd64789e57ee183233ea3a09e467ed2db4
  Stored in directory: /root/.cache/pip/wheels/72/17/52/9d818b4c60f733bf49d5cf82bc2758ebbdc57a0471137c37be
Successfully built GPyOpt
  Attempting uninstall: scipy
    Found existing installation: scipy 1.13.1
    Uninstalling scipy-1.13.1:
      Successfu

In [3]:
import numpy as np
import cv2
from skimage.metrics import structural_similarity
from sklearn.preprocessing import MinMaxScaler
import GPyOpt
from GPyOpt.methods import BayesianOptimization
import ot
import matplotlib.pyplot as plt
import skimage
from skimage.morphology import skeletonize
from skimage.measure import label, regionprops
from skimage.draw import circle_perimeter
from skimage.filters import threshold_otsu
from PIL import Image
from scipy.ndimage import convolve
from skimage.util import invert
from skimage.feature import corner_harris, corner_peaks
from scipy.spatial import distance_matrix
import gudhi as gd
from sklearn.cluster import KMeans
import os
import itertools
from scipy.stats import wasserstein_distance
import pandas as pd
import seaborn as sns
from skimage.metrics import structural_similarity as ssim
from google.colab import output
import base64

In [4]:
!nvidia-smi
HOME = os.getcwd()
print("HOME:", HOME)
!pip install -q 'git+https://github.com/facebookresearch/segment-anything.git'
!pip install -q jupyter_bbox_widget roboflow dataclasses-json supervision
!mkdir -p {HOME}/weights
!wget -q https://dl.fbaipublicfiles.com/segment_anything/sam_vit_h_4b8939.pth -P {HOME}/weights
CHECKPOINT_PATH = os.path.join(HOME, "weights", "sam_vit_h_4b8939.pth")
print(CHECKPOINT_PATH, "; exist:", os.path.isfile(CHECKPOINT_PATH))
!mkdir -p {HOME}/data

!wget -q https://media.roboflow.com/notebooks/examples/dog.jpeg -P {HOME}/data
!wget -q https://media.roboflow.com/notebooks/examples/dog-2.jpeg -P {HOME}/data
!wget -q https://media.roboflow.com/notebooks/examples/dog-3.jpeg -P {HOME}/data
!wget -q https://media.roboflow.com/notebooks/examples/dog-4.jpeg -P {HOME}/data

Thu Sep 19 21:47:11 2024       
+---------------------------------------------------------------------------------------+
| NVIDIA-SMI 535.104.05             Driver Version: 535.104.05   CUDA Version: 12.2     |
|-----------------------------------------+----------------------+----------------------+
| GPU  Name                 Persistence-M | Bus-Id        Disp.A | Volatile Uncorr. ECC |
| Fan  Temp   Perf          Pwr:Usage/Cap |         Memory-Usage | GPU-Util  Compute M. |
|                                         |                      |               MIG M. |
|=========================================+======================+======================|
|   0  Tesla T4                       Off | 00000000:00:04.0 Off |                    0 |
| N/A   41C    P8               9W /  70W |      0MiB / 15360MiB |      0%      Default |
|                                         |                      |                  N/A |
+-----------------------------------------+----------------------+--

In [5]:
import torch
from segment_anything import sam_model_registry, SamAutomaticMaskGenerator, SamPredictor
import supervision as sv

### SAM

In [19]:
name = "PMNS-576"
os.makedirs("/content/Matrix", exist_ok=True)
matrix_folder = "/content/Matrix"

In [8]:
# Optionally, move files from Google Drive to your desired directory in Colab
import shutil
shutil.copy(f'/content/{name}.JPG', f"{HOME}/data/{name}.JPG")

'/content/data/PMNS-576.JPG'

In [9]:
os.makedirs("/content/Segmented_images", exist_ok=True)

In [10]:
DEVICE = torch.device('cuda:0' if torch.cuda.is_available() else 'cpu')
MODEL_TYPE = "vit_h"
sam = sam_model_registry[MODEL_TYPE](checkpoint=CHECKPOINT_PATH).to(device=DEVICE)
mask_generator = SamAutomaticMaskGenerator(model=sam,
                                          )

In [11]:
IMAGE_NAME = f'{name}.JPG'
IMAGE_PATH = os.path.join(HOME, "data", IMAGE_NAME)

In [12]:
image_bgr = cv2.imread(IMAGE_PATH)
resized_image_bgr = cv2.resize(image_bgr,(image_bgr.shape[1] // 2,image_bgr.shape[0] // 2))
image_rgb = cv2.cvtColor(resized_image_bgr, cv2.COLOR_BGR2RGB)
torch.cuda.empty_cache()
sam_result = mask_generator.generate(image_rgb)
mask_annotator = sv.MaskAnnotator(color_lookup=sv.ColorLookup.INDEX)
detections = sv.Detections.from_sam(sam_result=sam_result)
annotated_image = mask_annotator.annotate(scene=resized_image_bgr.copy(), detections=detections)
masks = [
    mask['segmentation']
    for mask
    in sorted(sam_result, key=lambda x: x['area'], reverse=True)
]
mask_predictor = SamPredictor(sam)
resized_image_path = "/content/resized_image.jpg"
cv2.imwrite(resized_image_path, image_rgb)

# helper function that loads an image before adding it to the widget
def encode_image(filepath):
    with open(filepath, 'rb') as f:
        image_bytes = f.read()
    encoded = str(base64.b64encode(image_bytes), 'utf-8')
    return "data:image/jpg;base64,"+encoded


IS_COLAB = True
if IS_COLAB:
  output.enable_custom_widget_manager()
from jupyter_bbox_widget import BBoxWidget
widget = BBoxWidget()
widget.image = encode_image(resized_image_path)
widget

BBoxWidget(colors=['#1f77b4', '#ff7f0e', '#2ca02c', '#d62728', '#9467bd', '#8c564b', '#e377c2', '#7f7f7f', '#b…

In [13]:
# Get the bounding boxes from the widget (will assume 10 boxes)
bboxes = widget.bboxes if len(widget.bboxes) >= 10 else [None] * 10
if len(bboxes) < 10:
    print(f"Only {len(bboxes)} boxes drawn. Using default box for remaining boxes.")

# Set up SAM Predictor
mask_predictor = SamPredictor(sam)
image_bgr = cv2.imread(resized_image_path)
image_rgb = cv2.cvtColor(resized_image_bgr, cv2.COLOR_BGR2RGB)
mask_predictor.set_image(image_rgb)

# Iterate over all 10 bounding boxes and process each one
for idx, box in enumerate(bboxes[:10]):
    if box:
        # Extract coordinates from user-drawn box
        box = np.array([
            box['x'],
            box['y'],
            box['x'] + box['width'],
            box['y'] + box['height']
        ])
    else:
        # Default box in case the user hasn't provided enough boxes
        box = np.array([68, 247, 68 + 555, 247 + 678])

    masks, scores, logits = mask_predictor.predict(
        box=box,
        multimask_output=True
    )

    box_annotator = sv.BoxAnnotator(color=sv.Color.RED, color_lookup=sv.ColorLookup.INDEX)
    mask_annotator = sv.MaskAnnotator(color=sv.Color.RED, color_lookup=sv.ColorLookup.INDEX)

    detections = sv.Detections(
        xyxy=sv.mask_to_xyxy(masks=masks),
        mask=masks
    )

    if detections.mask.shape[0] > 0:
        detections = detections[detections.area == np.max(detections.area)]

        # Annotate the image
        source_image = box_annotator.annotate(scene=image_bgr.copy(), detections=detections)
        segmented_image = mask_annotator.annotate(scene=image_bgr.copy(), detections=detections)

        import supervision as v

        segmentation_mask = masks[2]
        # Display the source and segmented images

        # Ensure there are enough masks and select the third mask
        if len(masks) >= 3:
            chosen_mask = masks[2]  # Select the third mask
        elif masks:
            chosen_mask = masks[0]  # Fallback to the first mask if there are fewer than 3
        else:
            print(f"No masks found for box {idx+1}.")
            continue

        # Convert the mask to binary
        binary_mask = np.where(chosen_mask > 0.5, 1, 0).astype(np.uint8)

        # Find contours to get the bounding box of the segmented area
        contours, _ = cv2.findContours(binary_mask, cv2.RETR_EXTERNAL, cv2.CHAIN_APPROX_SIMPLE)

        if len(contours) > 0:
            x, y, w, h = cv2.boundingRect(contours[0])
            cropped_image = image_bgr[y:y+h, x:x+w]
            cropped_image_rgb = cv2.cvtColor(cropped_image, cv2.COLOR_BGR2RGB)
            # Save the segmented image
            index_str = f"{idx+1:02d}"  # Ensure two digits for sorting order
            segmented_image_path = f"/content/Segmented_images/{IMAGE_NAME.split('.')[0]}_box_{index_str}.jpg"
            cv2.imwrite(segmented_image_path, cropped_image_rgb)
            print(f"Saved segmented image: {segmented_image_path}")

Saved segmented image: /content/Segmented_images/PMNS-576_box_01.jpg
Saved segmented image: /content/Segmented_images/PMNS-576_box_02.jpg
Saved segmented image: /content/Segmented_images/PMNS-576_box_03.jpg
Saved segmented image: /content/Segmented_images/PMNS-576_box_04.jpg
Saved segmented image: /content/Segmented_images/PMNS-576_box_05.jpg
Saved segmented image: /content/Segmented_images/PMNS-576_box_06.jpg
Saved segmented image: /content/Segmented_images/PMNS-576_box_07.jpg
Saved segmented image: /content/Segmented_images/PMNS-576_box_08.jpg
Saved segmented image: /content/Segmented_images/PMNS-576_box_09.jpg
Saved segmented image: /content/Segmented_images/PMNS-576_box_10.jpg


### Distance Matrix

In [14]:

# Input and output directories
input_folder = '/content/Segmented_images/'  # Folder containing the input images
output_folder = '/content/Sketches/'  # Folder to save the output images

# Create output folder if it doesn't exist
os.makedirs(output_folder, exist_ok=True)

# Image preprocessing
def preprocess_image(image):
    if image is None:
        raise ValueError("Input image is None. Please check the image path.")

    # Convert to grayscale
    if len(image.shape) == 3:  # Check if the image has 3 channels (BGR)
        gray = cv2.cvtColor(image, cv2.COLOR_BGR2GRAY)
    else:
        gray = image  # If it's already grayscale, use it as is

    # Apply Gaussian blur to reduce noise
    blur = cv2.GaussianBlur(gray, (5, 5), 0)

    # Apply adaptive histogram equalization
    clahe = cv2.createCLAHE(clipLimit=2.0, tileGridSize=(8, 8))
    equalized = clahe.apply(blur)

    return equalized

# Helper function to compute Sinkhorn distance
def sinkhorn_distance(hist1, hist2, epsilon=0.1):
    M = ot.dist(hist1.reshape(-1, 1), hist2.reshape(-1, 1), metric='euclidean')
    return ot.sinkhorn2(hist1, hist2, M, reg=epsilon)

# Objective function for Bayesian optimization
def objective_function(params):
    sigma = params[0][0]
    alpha = params[0][1]
    beta = params[0][2]

    # Apply semantic sketching
    sketched = apply_semantic_sketching(fingerprint, sigma, alpha, beta)

    # Compute histogram of edge intensities
    hist, _ = np.histogram(fingerprint, bins=256, range=(0, 256), density=True)
    ref_hist, _ = np.histogram(sketched, bins=256, range=(0, 256), density=True)

    # Compute Sinkhorn distance
    distance = sinkhorn_distance(hist, ref_hist)
    return -distance

# Semantic sketching function
def apply_semantic_sketching(image, sigma, alpha, beta):
    # Preprocess the image
    processed_image = preprocess_image(image)

    # Apply Gaussian smoothing
    smoothed = cv2.GaussianBlur(processed_image, (0, 0), sigma)

    # Apply adaptive thresholding
    thresh = cv2.adaptiveThreshold(smoothed, 255, cv2.ADAPTIVE_THRESH_GAUSSIAN_C, cv2.THRESH_BINARY, 11, alpha)

    # Apply dilation and erosion
    kernel = np.ones((3, 3), np.uint8)
    dilated = cv2.dilate(thresh, kernel, iterations=1)
    eroded = cv2.erode(dilated, kernel, iterations=1)
    # Ensure both images have the same size and number of channels
    if eroded.shape != image.shape[:2]:  # Compare eroded to only the height and width of image
        eroded = cv2.resize(eroded, (image.shape[1], image.shape[0]))  # Resize to match original image dimensions

    # Convert image to the same number of channels if necessary
    if len(image.shape) == 3 and len(eroded.shape) == 2:  # If eroded is single channel
        eroded = cv2.cvtColor(eroded, cv2.COLOR_GRAY2BGR)
    # Adjust intensity
    adjusted = cv2.addWeighted(eroded, beta, image, 1 - beta, 0)

    return adjusted

# Process each image in the input folder
for filename in os.listdir(input_folder):
    if filename.endswith('.png') or filename.endswith('.jpg'):  # Add other formats if needed
        image_path = os.path.join(input_folder, filename)
        image = cv2.imread(image_path)

        # Check if the image loaded successfully
        if image is None:
            print(f"Failed to load image: {image_path}")
            continue

        # Preprocess input image
        fingerprint = preprocess_image(image)

        # Define hyperparameter bounds
        bounds = [{'name': 'sigma', 'type': 'continuous', 'domain': (0.1, 2)},
                  {'name': 'alpha', 'type': 'continuous', 'domain': (0.1, 2)},
                  {'name': 'beta', 'type': 'continuous', 'domain': (0.1, 2)}]

        # Perform Bayesian optimization
        optimizer = BayesianOptimization(f=objective_function, domain=bounds, maximize=False)
        optimizer.run_optimization(max_iter=80)

        # Get optimal hyperparameters
        optimal_params = optimizer.x_opt

        # Apply semantic sketching with optimal hyperparameters
        sketched = apply_semantic_sketching(image, *optimal_params)

        # Save the sketched image with the same filename in the output folder
        output_path = os.path.join(output_folder, filename)
        cv2.imwrite(output_path, sketched)
        print("Done")

Done
Done
Done
Done
Done
Done
Done
Done
Done
Done


In [17]:
import os
import cv2
import numpy as np
import skimage
from skimage.morphology import skeletonize
from skimage.measure import label, regionprops
from sklearn.cluster import KMeans
from scipy.spatial import distance_matrix
import gudhi as gd
import matplotlib.pyplot as plt
from io import BytesIO
from PIL import Image


# Function to detect ridges using Hessian matrix
def detect_ridges(gray, sigma=0.1):
    H_elems = skimage.feature.hessian_matrix(gray, sigma=sigma, order='rc')
    maxima_ridges, minima_ridges = skimage.feature.hessian_matrix_eigvals(H_elems)
    return maxima_ridges, minima_ridges

# Function to get termination and bifurcation points
def getTerminationBifurcation(img, mask):
    img = img == 255
    (rows, cols) = img.shape
    minutiaeTerm = np.zeros(img.shape)
    minutiaeBif = np.zeros(img.shape)

    for i in range(1, rows - 1):
        for j in range(1, cols - 1):
            if img[i][j] == 1:
                block = img[i - 1:i + 2, j - 1:j + 2]
                block_val = np.sum(block)
                if block_val == 2:
                    minutiaeTerm[i, j] = 1
                elif block_val == 4:
                    minutiaeBif[i, j] = 1

    mask = skimage.morphology.convex_hull_image(mask > 0)
    mask = skimage.morphology.erosion(mask, skimage.morphology.square(5))
    minutiaeTerm = np.uint8(mask) * minutiaeTerm
    return minutiaeTerm, minutiaeBif

class MinutiaeFeature:
    def __init__(self, locX, locY, Orientation, Type):
        self.locX = locX
        self.locY = locY
        self.Orientation = Orientation
        self.Type = Type

def computeAngle(block, minutiaeType):
    angle = 0
    (blkRows, blkCols) = np.shape(block)
    CenterX, CenterY = (blkRows - 1) / 2, (blkCols - 1) / 2
    if minutiaeType.lower() == 'termination':
        sumVal = 0
        for i in range(blkRows):
            for j in range(blkCols):
                if (i == 0 or i == blkRows - 1 or j == 0 or j == blkCols - 1) and block[i][j] != 0:
                    angle = -np.degrees(np.arctan2(i - CenterY, j - CenterX))
                    sumVal += 1
                    if sumVal > 1:
                        angle = float('nan')
        return angle
    elif minutiaeType.lower() == 'bifurcation':
        angle = []
        sumVal = 0
        for i in range(blkRows):
            for j in range(blkCols):
                if (i == 0 or i == blkRows - 1 or j == 0 or j == blkCols - 1) and block[i][j] != 0:
                    angle.append(-np.degrees(np.arctan2(i - CenterY, j - CenterX)))
                    sumVal += 1
        if sumVal != 3:
            angle = float('nan')
        return angle

def extractMinutiaeFeatures(skel, minutiaeTerm, minutiaeBif):
    FeaturesTerm = []
    minutiaeTerm = label(minutiaeTerm, connectivity=2)
    RP = regionprops(minutiaeTerm)
    WindowSize = 2
    for i in RP:
        (row, col) = np.int16(np.round(i['Centroid']))
        block = skel[row - WindowSize:row + WindowSize + 1, col - WindowSize:col + WindowSize + 1]
        angle = computeAngle(block, 'Termination')
        FeaturesTerm.append(MinutiaeFeature(row, col, angle, 'Termination'))

    FeaturesBif = []
    minutiaeBif = label(minutiaeBif, connectivity=2)
    RP = regionprops(minutiaeBif)
    WindowSize = 1
    for i in RP:
        (row, col) = np.int16(np.round(i['Centroid']))
        block = skel[row - WindowSize:row + WindowSize + 1, col - WindowSize:col + WindowSize + 1]
        angle = computeAngle(block, 'Bifurcation')
        FeaturesBif.append(MinutiaeFeature(row, col, angle, 'Bifurcation'))
    return FeaturesTerm, FeaturesBif

def AddMinutiae(skel, TermLabel, BifLabel, FeaturesTerm, FeaturesBif):
    minutiae_points = []
    for feature in FeaturesTerm + FeaturesBif:
        minutiae_points.append([feature.locX, feature.locY])
    return minutiae_points

def reduce_minutiae_points(points, max_points=100):
    points = np.array(points)  # Ensure points is a NumPy array
    if len(points) > max_points:
        kmeans = KMeans(n_clusters=max_points, random_state=0).fit(points)
        reduced_points = kmeans.cluster_centers_
    else:
        reduced_points = points
    return reduced_points

def compute_distance_matrix(points):
    points = np.array(points)  # Ensure points is a NumPy array
    if points.ndim == 1:  # If points are 1D, convert to 2D
        points = points.reshape(-1, 1)
    return distance_matrix(points, points)

def construct_vietoris_rips_filtration(dist_matrix, max_dimension=1, max_filtration_value=np.inf):
    rips_complex = gd.RipsComplex(distance_matrix=dist_matrix, max_edge_length=max_filtration_value)
    simplex_tree = rips_complex.create_simplex_tree(max_dimension=max_dimension)
    return simplex_tree

def compute_persistent_homology(simplex_tree):
    return simplex_tree.persistence()

# Function to process all images in the input folder
def barcode_images(input_folder, output_folder):
    if not os.path.exists(output_folder):
        os.makedirs(output_folder)

    for filename in os.listdir(input_folder):
        if filename.endswith(".png") or filename.endswith(".jpg"):
            img_path = os.path.join(input_folder, filename)
            img = cv2.imread(img_path, 0)
            if img is None:
                print(f"Error loading image: {img_path}")
                continue

            # Apply Otsu's thresholding
            ret, img_bin = cv2.threshold(img, 0, 255, cv2.THRESH_BINARY + cv2.THRESH_OTSU)

            # Skeletonize the binary image
            skel = skeletonize(img_bin // 255)
            skel = np.uint8(skel) * 255

            # Create a mask from the binary image
            mask = img_bin * 255

            # Get termination and bifurcation points
            minutiaeTerm, minutiaeBif = getTerminationBifurcation(skel, mask)
            FeaturesTerm, FeaturesBif = extractMinutiaeFeatures(skel, minutiaeTerm, minutiaeBif)

            # Label the features for visualization
            BifLabel = label(minutiaeBif, connectivity=1)
            TermLabel = label(minutiaeTerm, connectivity=1)
            minutiae_points = AddMinutiae(skel, TermLabel, BifLabel, FeaturesTerm, FeaturesBif)

            # Reduce the number of minutiae points
            reduced_minutiae_points = reduce_minutiae_points(minutiae_points, max_points=100)

            # Compute the distance matrix and construct the Vietoris-Rips filtration
            dist_matrix = compute_distance_matrix(reduced_minutiae_points)
            simplex_tree = construct_vietoris_rips_filtration(dist_matrix)

            # Compute the persistent homology and plot the barcode
            persistence = compute_persistent_homology(simplex_tree)

            # Save the plot to the output folder with the same name as the input image
            plt.figure()
            gd.plot_persistence_barcode(persistence)
            output_image_path = os.path.join(output_folder, f"{os.path.splitext(filename)[0]}_barcode.jpg")
            plt.savefig(output_image_path)  # Save the figure to the output folder
            plt.close()  # Close the figure to avoid display

            print(f"Processed and saved barcode for {filename}.")


# Example usage
input_folder = 'Sketches/'  # Replace with the path to the input folder
output_folder = 'Barcode/'  # Replace with the path to the output folder
barcode_images(input_folder, output_folder)

Processed and saved barcode for PMNS-576_box_09.jpg.
Processed and saved barcode for PMNS-576_box_05.jpg.
Processed and saved barcode for PMNS-576_box_04.jpg.
Processed and saved barcode for PMNS-576_box_03.jpg.
Processed and saved barcode for PMNS-576_box_10.jpg.
Processed and saved barcode for PMNS-576_box_07.jpg.
Processed and saved barcode for PMNS-576_box_02.jpg.
Processed and saved barcode for PMNS-576_box_08.jpg.
Processed and saved barcode for PMNS-576_box_06.jpg.
Processed and saved barcode for PMNS-576_box_01.jpg.


<Figure size 640x480 with 0 Axes>

<Figure size 640x480 with 0 Axes>

<Figure size 640x480 with 0 Axes>

<Figure size 640x480 with 0 Axes>

...

<Figure size 640x480 with 0 Axes>

<Figure size 640x480 with 0 Axes>

<Figure size 640x480 with 0 Axes>

<Figure size 640x480 with 0 Axes>

<Figure size 640x480 with 0 Axes>

In [20]:
import os
import numpy as np
import matplotlib.pyplot as plt
import pandas as pd
import seaborn as sns
import itertools
from scipy.stats import wasserstein_distance
from PIL import Image

# Function to check if a barcode is valid
def is_valid_barcode(barcode):
    return len(barcode) > 0 and np.isfinite(barcode).all()

# Function to filter out infinite values from barcode
def filter_inf_values(barcode):
    return barcode[np.isfinite(barcode).all(axis=1)]

# Function to compute distance matrix between barcodes
def compute_distance_matrix_between_barcodes(barcodes):
    num_barcodes = len(barcodes)
    distance_matrix = np.zeros((num_barcodes, num_barcodes))
    for i, j in itertools.combinations(range(num_barcodes), 2):
        filtered_barcode_i = filter_inf_values(barcodes[i])
        filtered_barcode_j = filter_inf_values(barcodes[j])
        if not is_valid_barcode(filtered_barcode_i) or not is_valid_barcode(filtered_barcode_j):
            distance = np.inf  # Assign a large distance if any barcode is invalid
        else:
            distance = wasserstein_distance(filtered_barcode_i.flatten(), filtered_barcode_j.flatten())
        distance_matrix[i, j] = distance
        distance_matrix[j, i] = distance
    return distance_matrix

# Function to load images from a folder and convert them to numpy arrays (assuming barcodes are saved as images)
def load_images_from_folder(folder):
    images = []
    for filename in os.listdir(folder):
        if filename.endswith(".png") or filename.endswith(".jpg"):
            img_path = os.path.join(folder, filename)
            img = Image.open(img_path)
            img_array = np.array(img.convert('L'))  # Convert image to grayscale
            images.append(img_array)
    return images

# Main function to process images, compute the distance matrix, and save it as an image
def process_and_save_distance_matrix(input_folder, output_image_name):
    # Load barcode images from the folder
    barcode_images = load_images_from_folder(input_folder)

    # Ensure that the barcodes are lists of birth-death pairs (convert to numpy arrays)
    for i, barcode in enumerate(barcode_images):
        barcode_images[i] = np.array(barcode)

    # Compute the distance matrix between persistence barcodes
    dist_matrix_barcodes = compute_distance_matrix_between_barcodes(barcode_images)

    # Create a DataFrame for better visualization and understanding
    dist_matrix_df = pd.DataFrame(dist_matrix_barcodes)

    # Create a heatmap to visualize the distance matrix
    plt.figure(figsize=(10, 8))
    sns.heatmap(dist_matrix_df, annot=True, fmt=".2f", cmap="viridis", xticklabels=False, yticklabels=False)
    plt.title("Distance Matrix Between Persistence Barcodes")

    # Save the heatmap as an image
    output_path = os.path.join(matrix_folder, output_image_name)
    plt.savefig(output_path)
    plt.close()
    print(f"Distance matrix saved as {output_path}")

# Example usage
input_folder = 'Barcode/'  # Replace with your folder path
output_image_name = f'distance_matrix_{name}.png'  # Desired name for the output image
process_and_save_distance_matrix(input_folder, output_image_name)

Distance matrix saved as /content/Matrix/distance_matrix_PMNS-576.png
